In [4]:
# pip install BeautifulSoup4
# pip install pandas
# pip install numpy
# pip install selenium
# pip instal webdriver_manager (este se usa para descargar automaticamente ChromeDriverManager en la misma versión que tu Google Chrome)
# y es necesario porque necesitamos un driver.get(url)

In [1]:
from bs4 import BeautifulSoup, SoupStrainer
import pandas as pd
import numpy as np

# Driver de selenium
from selenium import webdriver
from selenium.webdriver.chrome.options import Options # Para modificar las opciones de WebDriver en Chrome
from selenium.webdriver.chrome.service import Service

# Para instalar automáticamente el ChromeDriver correspondiente
from webdriver_manager.chrome import ChromeDriverManager 

In [2]:
url = "https://fbref.com/es/comps/12/stats/Estadisticas-de-La-Liga"

# Instalamos la version de ChromeDriver correspondiente (debe coincidir con nuestra versión de chrome).
# Nos devuelve la ruta donde lo guarda

ruta = ChromeDriverManager().install()

# Definimos las opciones de nuestro navegador Chrome

options = Options()

user_agent = "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/119.0.0.0 Safari/537.36"
options.add_argument(f"user-agent = {user_agent}") # Defino un user agent predeterminado. Sospecho que solo funciona
# escribiendo el user agent de quien haga uso de este cuaderno, o dejando el por defecto (se quita esta opción y ya)

# Se pueden añadir muchas más opciones (a gusto del consumidor), las que a mi me gustan son estas:

options.add_argument("--disable-notifications") # Deshabilitamos notificaciones.
options.add_argument("--no-first-run") # Para que no ejecute tareas que se ejecutan la primera vez que runeas Chrome
options.add_argument("--disable-blink-features=AutomationControlled") # Evita que el servidor no detecte que somos un bot

# Vamos a abrir nuestra web :)

s = Service(ruta)
driver = webdriver.Chrome(service = s, options = options)
driver.get(url)

In [3]:
# Ahora empezamos a hacer uso de BeautifulSoup para encontrar elementos del codigo html de la página.
# Lo primero creo mi sopa

soup = BeautifulSoup(driver.page_source, "html.parser")

# El atributo page_source es el html. Ahora mismo mi sopa es básicamente un string con el código fuente donde podemos
# encontrar elementos. Pues vamos a buscarlos con el método find() y find_all()

soup.find_all("tbody") # ¿por qué busco este elemento?

# Busco todos los elementos del html que sean del tipo <tbody> porque las dos tablas que me interesa obtener tienen
# como elemento padre este <tbody>. Este método me ha devuelto una lista en la que cada uno de los elementos son 
# cada una de las estructuras <tbody> que hay en el código fuente. Pues bueno, si hacemos command (ctrl) + F en el 
# html nos permite buscar "tbody" para encontrar cuantos hay en el código html. En nuestro caso, los <tbody> que
# contienen las tablas que nosotros queremos obtener son el 9 y el 11. Pues vamos a extraer esos dos elementos.

[<tbody><tr>
 <td><a href="/es/equipos/b8fd03ef/Estadisticas-de-Manchester-City">Manchester City</a></td>
 <td>88 pts.</td>
 <td><a href="/es/equipos/b8fd03ef/historia/Estadisticas-e-historial-de-Manchester-City">Club</a></td>
 </tr>
 <tr>
 <td><a href="/es/equipos/18bb7c10/Estadisticas-de-Arsenal">Arsenal</a></td>
 <td>86 pts.</td>
 <td><a href="/es/equipos/18bb7c10/historia/Estadisticas-e-historial-de-Arsenal">Club</a></td>
 </tr>
 <tr>
 <td><a href="/es/equipos/822bd0ba/Estadisticas-de-Liverpool">Liverpool</a></td>
 <td>79 pts.</td>
 <td><a href="/es/equipos/822bd0ba/historia/Estadisticas-e-historial-de-Liverpool">Club</a></td>
 </tr>
 <tr>
 <td><a href="/es/equipos/8602292d/Estadisticas-de-Aston-Villa">Aston Villa</a></td>
 <td>68 pts.</td>
 <td><a href="/es/equipos/8602292d/historia/Estadisticas-e-historial-de-Aston-Villa">Club</a></td>
 </tr>
 </tbody>,
 <tbody><tr>
 <td><a href="/es/equipos/d609edc0/Estadisticas-de-Internazionale">Internazionale</a></td>
 <td>92 pts.</td>
 <td><

In [4]:
tabla_equipos_html = soup.find_all("tbody")[9]
tabla_jugadores_html = soup.find_all("tbody")[11]

In [5]:
# Inspeccionemos estos dos elementos para poder sustraer de ahí las filas con datos:
tabla_equipos_html
# Cada fila de la tabla es un <tr data-row=""> y dentro de cada fila, cada columna es un <td data-stat="">

<tbody> <tr data-row="0"><th class="left" data-stat="team" scope="row"><a href="/es/equipos/8d6fd021/Estadisticas-de-Alaves">Alavés</a></th><td class="right" data-stat="players_used">29</td><td class="center" data-stat="avg_age">26.4</td><td class="center" data-stat="possession">41.9</td><td class="right iz group_start" data-stat="games"></td><td class="right" data-stat="games_starts">396</td><td class="right" csk="3240" data-stat="minutes">3,240</td><td class="right" data-stat="minutes_90s">36.0</td><td class="right group_start" data-stat="goals">31</td><td class="right" data-stat="assists">26</td><td class="right" data-stat="goals_assists">57</td><td class="right" data-stat="goals_pens">28</td><td class="right" data-stat="pens_made">3</td><td class="right" data-stat="pens_att">6</td><td class="right" data-stat="cards_yellow">78</td><td class="right" data-stat="cards_red">1</td><td class="right group_start" data-stat="xg">42.5</td><td class="right" data-stat="npxg">37.8</td><td class=

In [6]:
tabla_jugadores_html
# En este caso es igual. ¿Qué habría que hacer en ambos casos? Pues un find_all de los tr y dentro de cada elemento
# de la lista que nos devuelve, find_all de los td

<tbody><tr data-row="0"><th class="right" data-stat="ranker" scope="row">1</th><td class="left" csk="Abner" data-append-csv="7f9c5d2d" data-stat="player"><a href="/es/jugadores/7f9c5d2d/Abner">Abner</a></td><td class="left poptip" data-stat="nationality" data-tip="YNT"><a href="/es/pais/BRA/Futbol-de-Brazil"><span style="white-space: nowrap"><span class="f-i f-br" style="">br</span> BRA</span></a></td><td class="center" csk="2.0" data-stat="position">DF</td><td class="left" data-stat="team"><a href="/es/equipos/fc536746/Estadisticas-de-Real-Betis">Betis</a></td><td class="center" data-stat="age">23-356</td><td class="center" data-stat="birth_year">2000</td><td class="right group_start" data-stat="games">22</td><td class="right" data-stat="games_starts">14</td><td class="right" csk="1310" data-stat="minutes">1,310</td><td class="right" data-stat="minutes_90s">14.6</td><td class="right iz group_start" data-stat="goals">0</td><td class="right iz" data-stat="assists">0</td><td class="right

In [7]:
tabla_equipos_html_filas = tabla_equipos_html.find_all("tr") # Esto nos ha devuelto una lista donde cada elemento
# es el html de cada fila de la tabla de las estadisticas por equipos
tabla_equipos_html_filas[0].find_all("td") # Y por ejemplo, aquí accedemos al primer elemento, que es el primer equipo
# con todas sus estadísticas y nos devuelve una lista donde cada elemento es cada estadística.

[<td class="right" data-stat="players_used">29</td>,
 <td class="center" data-stat="avg_age">26.4</td>,
 <td class="center" data-stat="possession">41.9</td>,
 <td class="right iz group_start" data-stat="games"></td>,
 <td class="right" data-stat="games_starts">396</td>,
 <td class="right" csk="3240" data-stat="minutes">3,240</td>,
 <td class="right" data-stat="minutes_90s">36.0</td>,
 <td class="right group_start" data-stat="goals">31</td>,
 <td class="right" data-stat="assists">26</td>,
 <td class="right" data-stat="goals_assists">57</td>,
 <td class="right" data-stat="goals_pens">28</td>,
 <td class="right" data-stat="pens_made">3</td>,
 <td class="right" data-stat="pens_att">6</td>,
 <td class="right" data-stat="cards_yellow">78</td>,
 <td class="right" data-stat="cards_red">1</td>,
 <td class="right group_start" data-stat="xg">42.5</td>,
 <td class="right" data-stat="npxg">37.8</td>,
 <td class="right" data-stat="xg_assist">29.6</td>,
 <td class="right" data-stat="npxg_xg_assist">6

In [8]:
# Con la tabla de jugadores igual.

tabla_jugadores_html_filas = tabla_jugadores_html.find_all("tr") # Esto nos ha devuelto una lista donde cada elemento
# es el html de cada fila de la tabla de las estadisticas por jugador
tabla_jugadores_html_filas

[<tr data-row="0"><th class="right" data-stat="ranker" scope="row">1</th><td class="left" csk="Abner" data-append-csv="7f9c5d2d" data-stat="player"><a href="/es/jugadores/7f9c5d2d/Abner">Abner</a></td><td class="left poptip" data-stat="nationality" data-tip="YNT"><a href="/es/pais/BRA/Futbol-de-Brazil"><span style="white-space: nowrap"><span class="f-i f-br" style="">br</span> BRA</span></a></td><td class="center" csk="2.0" data-stat="position">DF</td><td class="left" data-stat="team"><a href="/es/equipos/fc536746/Estadisticas-de-Real-Betis">Betis</a></td><td class="center" data-stat="age">23-356</td><td class="center" data-stat="birth_year">2000</td><td class="right group_start" data-stat="games">22</td><td class="right" data-stat="games_starts">14</td><td class="right" csk="1310" data-stat="minutes">1,310</td><td class="right" data-stat="minutes_90s">14.6</td><td class="right iz group_start" data-stat="goals">0</td><td class="right iz" data-stat="assists">0</td><td class="right iz" d

In [9]:
tabla_jugadores_html_filas[0].find_all("td") # Y por ejemplo, aquí accedemos al primer elemento, que es el primer jugador
# con todas sus estadísticas y nos devuelve una lista donde cada elemento es cada estadística.

[<td class="left" csk="Abner" data-append-csv="7f9c5d2d" data-stat="player"><a href="/es/jugadores/7f9c5d2d/Abner">Abner</a></td>,
 <td class="left poptip" data-stat="nationality" data-tip="YNT"><a href="/es/pais/BRA/Futbol-de-Brazil"><span style="white-space: nowrap"><span class="f-i f-br" style="">br</span> BRA</span></a></td>,
 <td class="center" csk="2.0" data-stat="position">DF</td>,
 <td class="left" data-stat="team"><a href="/es/equipos/fc536746/Estadisticas-de-Real-Betis">Betis</a></td>,
 <td class="center" data-stat="age">23-356</td>,
 <td class="center" data-stat="birth_year">2000</td>,
 <td class="right group_start" data-stat="games">22</td>,
 <td class="right" data-stat="games_starts">14</td>,
 <td class="right" csk="1310" data-stat="minutes">1,310</td>,
 <td class="right" data-stat="minutes_90s">14.6</td>,
 <td class="right iz group_start" data-stat="goals">0</td>,
 <td class="right iz" data-stat="assists">0</td>,
 <td class="right iz" data-stat="goals_assists">0</td>,
 <t

In [10]:
# Lo que nos interesa es el texto de cada elemento ¿Como accedemos? con .text a cada elemento
tabla_jugadores_html_filas[0].find_all("td")[0].text

'Abner'

In [11]:
# Con los equipos igual
tabla_equipos_html_filas[0].find_all("td")[0].text

'29'

In [12]:
# Bueno, pues ahora podemos rellenar listas con estos datos en formato string a través de un bucle for
# Primero tabla de jugadores

tabla_jugadores = []
filas_html = []

for elemento in tabla_jugadores_html_filas: #Cada fila en html la mete en una lista de filas
    
    fila_n_html = elemento.find_all("td")
    filas_html.append(fila_n_html)
    
# Ahora tengo una lista que es cada fila de la tabla en html y cada elemento es a su vez una lista con cada estadística

for elemento in filas_html:
    
    if len(elemento) == 36: # Hay elementos que son listas vacias (separación de tabla), por eso compruebo que tenga longitud
        
        for element in elemento: #Para cada estadistica en html dentro de cada fila de la tabla en html, cojo el texto
            
            tabla_jugadores.append(element.text)
            
    else:
        
        pass
     


In [13]:
#Veamos nuestra lista con todos los datos
tabla_jugadores

['Abner',
 'br BRA',
 'DF',
 'Betis',
 '23-356',
 '2000',
 '22',
 '14',
 '1,310',
 '14.6',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '3',
 '0',
 '0.1',
 '0.1',
 '0.6',
 '0.7',
 '14',
 '31',
 '57',
 '0.00',
 '0.00',
 '0.00',
 '0.00',
 '0.00',
 '0.01',
 '0.04',
 '0.05',
 '0.01',
 '0.05',
 'Partidos',
 'Abdel Abqar',
 'ma MAR',
 'DF',
 'Alavés',
 '25-068',
 '1999',
 '25',
 '25',
 '2,177',
 '24.2',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '10',
 '0',
 '0.3',
 '0.3',
 '0.1',
 '0.4',
 '7',
 '48',
 '0',
 '0.00',
 '0.00',
 '0.00',
 '0.00',
 '0.00',
 '0.01',
 '0.00',
 '0.02',
 '0.01',
 '0.02',
 'Partidos',
 'Marcos Acuña',
 'ar ARG',
 'DF',
 'Sevilla',
 '32-202',
 '1991',
 '20',
 '17',
 '1,247',
 '13.9',
 '1',
 '2',
 '3',
 '1',
 '0',
 '0',
 '7',
 '0',
 '0.3',
 '0.3',
 '1.6',
 '1.9',
 '23',
 '57',
 '38',
 '0.07',
 '0.14',
 '0.22',
 '0.07',
 '0.22',
 '0.02',
 '0.11',
 '0.14',
 '0.02',
 '0.14',
 'Partidos',
 'Julen Agirrezabala',
 'es ESP',
 'PO',
 'Athletic Club',
 '23-143',
 '2000',
 '2',
 '1',
 '119',
 

In [14]:
# Vamos a hacer una lista en formato "tabla" para meterlo al data frame, que ahora mismo tengo una lista con todos
# los datos de seguido
len(tabla_jugadores)

21420

In [15]:
num_columnas = 36
num_filas = len(tabla_jugadores) // num_columnas

# Asegurémonos de que la longitud de la lista sea un múltiplo de 36
tabla_jugadores = tabla_jugadores[:num_filas * num_columnas]

# Reshape de la lista en un arreglo bidimensional de 36 columnas
data = [tabla_jugadores[i:i + num_columnas] for i in range(0, len(tabla_jugadores), num_columnas)]

#Veamos como ahora tengo una lista de listas
data

[['Abner',
  'br BRA',
  'DF',
  'Betis',
  '23-356',
  '2000',
  '22',
  '14',
  '1,310',
  '14.6',
  '0',
  '0',
  '0',
  '0',
  '0',
  '0',
  '3',
  '0',
  '0.1',
  '0.1',
  '0.6',
  '0.7',
  '14',
  '31',
  '57',
  '0.00',
  '0.00',
  '0.00',
  '0.00',
  '0.00',
  '0.01',
  '0.04',
  '0.05',
  '0.01',
  '0.05',
  'Partidos'],
 ['Abdel Abqar',
  'ma MAR',
  'DF',
  'Alavés',
  '25-068',
  '1999',
  '25',
  '25',
  '2,177',
  '24.2',
  '0',
  '0',
  '0',
  '0',
  '0',
  '0',
  '10',
  '0',
  '0.3',
  '0.3',
  '0.1',
  '0.4',
  '7',
  '48',
  '0',
  '0.00',
  '0.00',
  '0.00',
  '0.00',
  '0.00',
  '0.01',
  '0.00',
  '0.02',
  '0.01',
  '0.02',
  'Partidos'],
 ['Marcos Acuña',
  'ar ARG',
  'DF',
  'Sevilla',
  '32-202',
  '1991',
  '20',
  '17',
  '1,247',
  '13.9',
  '1',
  '2',
  '3',
  '1',
  '0',
  '0',
  '7',
  '0',
  '0.3',
  '0.3',
  '1.6',
  '1.9',
  '23',
  '57',
  '38',
  '0.07',
  '0.14',
  '0.22',
  '0.07',
  '0.22',
  '0.02',
  '0.11',
  '0.14',
  '0.02',
  '0.14',
  'P

In [16]:
# Creamos el DataFrame
# Primero necesitamos las columnas.

columnas_html = soup.find_all("th", scope = "col") # A partir del elemento 65 está lo que buscamos, antes están
# las columnas las estadisticas de la tabla de equipos

columnas_tabla_jugadores = []

for i in range (65,101):
    
    columnas_tabla_jugadores.append(columnas_html[i].text)

df = pd.DataFrame(data, columns = columnas_tabla_jugadores)
df

Jugador    País   Posc         Equipo    Edad Nacimiento  PJ  \
0                 Abner  br BRA     DF          Betis  23-356       2000  22   
1           Abdel Abqar  ma MAR     DF         Alavés  25-068       1999  25   
2          Marcos Acuña  ar ARG     DF        Sevilla  32-202       1991  20   
3    Julen Agirrezabala  es ESP     PO  Athletic Club  23-143       2000   2   
4         Lucien Agoume  fr FRA     CC        Sevilla  22-098       2002  10   
..                  ...     ...    ...            ...     ...        ...  ..   
590     Arsen Zakharyan  ru RUS  CC,DL  Real Sociedad  20-357       2003  26   
591       Joseba Zaldúa  es ESP  DF,CC          Cádiz  31-328       1992  11   
592      Bryan Zaragoza  es ESP  CC,DL        Granada  23-022       2001  21   
593       Igor Zubeldia  es ESP     DF  Real Sociedad  27-048       1997  30   
594    Martín Zubimendi  es ESP     CC  Real Sociedad  25-105       1999  31   

    Titular    Mín  90 s  ...   Ast   G+A  G-TP G+A-TP    xG   xAG xG+xAG  \
0        14  1,310  14.6  ...  0.00  0.00  0.00   0.00  0.01  0.04   0.05   
1        25  2,177  24.2  ...  0.00  0.00  0.00   0.00  0.01  0.00   0.02   
2        17  1,247  13.9  ...  0.14  0.22  0.07   0.22  0.02  0.11   0.14   
3         1    119   1.3  ...  0.00  0.00  0.00   0.00  0.00  0.00   0.00   
4         7    609   6.8  ...  0.00  0.00  0.00   0.00  0.02  0.05   0.07   
..      ...    ...   ...  ...   ...   ...   ...    ...   ...   ...    ...   
590      13  1,092  12.1  ...  0.16  0.25  0.08   0.25  0.19  0.16   0.35   
591       7    534   5.9  ...  0.00  0.00  0.00   0.00  0.00  0.04   0.04   
592      18  1,638  18.2  ...  0.11  0.44  0.27   0.38  0.21  0.18   0.39   
593      29  2,518  28.0  ...  0.07  0.07  0.00   0.07  0.03  0.04   0.07   
594      29  2,654  29.5  ...  0.03  0.17  0.14   0.17  0.09  0.05   0.14   

     npxG npxG+xAG  Partidos  
0    0.01     0.05  Partidos  
1    0.01     0.02  Partidos  
2    0.02     0.14  Partidos  
3    0.00     0.00  Partidos  
4    0.02     0.07  Partidos  
..    ...      ...       ...  
590  0.19     0.35  Partidos  
591  0.00     0.04  Partidos  
592  0.16     0.35  Partidos  
593  0.03     0.07  Partidos  
594  0.09     0.14  Partidos  

[595 rows x 36 columns]

In [67]:
columnas_tabla_jugadores
# Lo dejo por aquí porque es útil para buscar por el dataframe

['Jugador',
 'País',
 'Posc',
 'Equipo',
 'Edad',
 'Nacimiento',
 'PJ',
 'Titular',
 'Mín',
 '90 s',
 'Gls.',
 'Ass',
 'G+A',
 'G-TP',
 'TP',
 'TPint',
 'TA',
 'TR',
 'xG',
 'npxG',
 'xAG',
 'npxG+xAG',
 'PrgC',
 'PrgP',
 'PrgR',
 'Gls.',
 'Ast',
 'G+A',
 'G-TP',
 'G+A-TP',
 'xG',
 'xAG',
 'xG+xAG',
 'npxG',
 'npxG+xAG',
 'Partidos']

In [68]:
# Vamos a crear la tabla de las estadísticas por equipos

tabla_equipos = []
filas_equipos_html = []

for elemento in tabla_equipos_html_filas: #Cada fila en html la mete en una lista de filas
    
    fila_n_equipos_html = elemento.find_all("td")
    filas_equipos_html.append(fila_n_equipos_html)
    
# Ahora tengo una lista que es cada fila de la tabla en html y cada elemento es a su vez una lista con cada estadística

for elemento in filas_equipos_html:
    
    for element in elemento: #Para cada estadistica en html dentro de cada fila de la tabla en html, cojo el texto
            
        tabla_equipos.append(element.text)


In [69]:
tabla_equipos

['22',
 '26.9',
 '44.0',
 '11',
 '121',
 '990',
 '11.0',
 '7',
 '7',
 '14',
 '7',
 '0',
 '1',
 '27',
 '1',
 '13.5',
 '12.7',
 '9.5',
 '22.2',
 '162',
 '393',
 '0.64',
 '0.64',
 '1.27',
 '0.64',
 '1.27',
 '1.23',
 '0.86',
 '2.09',
 '1.15',
 '2.02',
 '27',
 '25.6',
 '48.4',
 '11',
 '121',
 '990',
 '11.0',
 '14',
 '9',
 '23',
 '13',
 '1',
 '1',
 '24',
 '1',
 '16.2',
 '15.4',
 '11.7',
 '27.1',
 '180',
 '343',
 '1.27',
 '0.82',
 '2.09',
 '1.18',
 '2.00',
 '1.47',
 '1.06',
 '2.53',
 '1.40',
 '2.46',
 '23',
 '28.0',
 '51.9',
 '11',
 '121',
 '990',
 '11.0',
 '18',
 '13',
 '31',
 '16',
 '2',
 '2',
 '31',
 '2',
 '16.7',
 '15.1',
 '12.4',
 '27.5',
 '209',
 '449',
 '1.64',
 '1.18',
 '2.82',
 '1.45',
 '2.64',
 '1.52',
 '1.13',
 '2.65',
 '1.38',
 '2.50',
 '22',
 '29.7',
 '51.3',
 '11',
 '121',
 '990',
 '11.0',
 '26',
 '16',
 '42',
 '24',
 '2',
 '2',
 '28',
 '1',
 '19.0',
 '17.5',
 '15.0',
 '32.5',
 '197',
 '444',
 '2.36',
 '1.45',
 '3.82',
 '2.18',
 '3.64',
 '1.72',
 '1.36',
 '3.08',
 '1.59',
 '2.96

In [70]:
num_columnas_equipos = 31
num_filas_equipos = len(tabla_equipos) // num_columnas_equipos

# Asegurémonos de que la longitud de la lista sea un múltiplo de 31
tabla_equipos = tabla_equipos[:num_filas_equipos * num_columnas_equipos]

# Reshape de la lista en un arreglo bidimensional de 31 columnas
data_equipos = [tabla_equipos[i:i + num_columnas_equipos] for i in range(0, len(tabla_equipos), num_columnas_equipos)]

#Veamos como ahora tengo una lista de listas
data_equipos

[['22',
  '26.9',
  '44.0',
  '11',
  '121',
  '990',
  '11.0',
  '7',
  '7',
  '14',
  '7',
  '0',
  '1',
  '27',
  '1',
  '13.5',
  '12.7',
  '9.5',
  '22.2',
  '162',
  '393',
  '0.64',
  '0.64',
  '1.27',
  '0.64',
  '1.27',
  '1.23',
  '0.86',
  '2.09',
  '1.15',
  '2.02'],
 ['27',
  '25.6',
  '48.4',
  '11',
  '121',
  '990',
  '11.0',
  '14',
  '9',
  '23',
  '13',
  '1',
  '1',
  '24',
  '1',
  '16.2',
  '15.4',
  '11.7',
  '27.1',
  '180',
  '343',
  '1.27',
  '0.82',
  '2.09',
  '1.18',
  '2.00',
  '1.47',
  '1.06',
  '2.53',
  '1.40',
  '2.46'],
 ['23',
  '28.0',
  '51.9',
  '11',
  '121',
  '990',
  '11.0',
  '18',
  '13',
  '31',
  '16',
  '2',
  '2',
  '31',
  '2',
  '16.7',
  '15.1',
  '12.4',
  '27.5',
  '209',
  '449',
  '1.64',
  '1.18',
  '2.82',
  '1.45',
  '2.64',
  '1.52',
  '1.13',
  '2.65',
  '1.38',
  '2.50'],
 ['22',
  '29.7',
  '51.3',
  '11',
  '121',
  '990',
  '11.0',
  '26',
  '16',
  '42',
  '24',
  '2',
  '2',
  '28',
  '1',
  '19.0',
  '17.5',
  '15.0'

In [71]:
# En esa data, falta una columna con los nombre de los equipos, que no aparece porque justo esa columna es una estructura
# <th> con unos atributos diferentes. Vamos a buscarla.
nombres_equipos_html = soup.find_all("th", scope = "row") # Los primeros 20 son los nombres de nuestros equipos.
nombres_equipos = []

for i in range(0,20):
    
    nombres_equipos.append(nombres_equipos_html[i].text)

nombres_equipos


['Alavés',
 'Almería',
 'Athletic Club',
 'Atlético Madrid',
 'Barcelona',
 'Betis',
 'Cádiz',
 'Celta Vigo',
 'Getafe',
 'Girona',
 'Granada',
 'Las Palmas',
 'Mallorca',
 'Osasuna',
 'Rayo Vallecano',
 'Real Madrid',
 'Real Sociedad',
 'Sevilla',
 'Valencia',
 'Villarreal']

In [72]:
# Dejemos por fin nuestra tabla de equipos con su lista bien hecha, con el nombre:

for i in range(len(data_equipos)):
    data_equipos[i].insert(0, nombres_equipos[i])
    
data_equipos

[['Alavés',
  '22',
  '26.9',
  '44.0',
  '11',
  '121',
  '990',
  '11.0',
  '7',
  '7',
  '14',
  '7',
  '0',
  '1',
  '27',
  '1',
  '13.5',
  '12.7',
  '9.5',
  '22.2',
  '162',
  '393',
  '0.64',
  '0.64',
  '1.27',
  '0.64',
  '1.27',
  '1.23',
  '0.86',
  '2.09',
  '1.15',
  '2.02'],
 ['Almería',
  '27',
  '25.6',
  '48.4',
  '11',
  '121',
  '990',
  '11.0',
  '14',
  '9',
  '23',
  '13',
  '1',
  '1',
  '24',
  '1',
  '16.2',
  '15.4',
  '11.7',
  '27.1',
  '180',
  '343',
  '1.27',
  '0.82',
  '2.09',
  '1.18',
  '2.00',
  '1.47',
  '1.06',
  '2.53',
  '1.40',
  '2.46'],
 ['Athletic Club',
  '23',
  '28.0',
  '51.9',
  '11',
  '121',
  '990',
  '11.0',
  '18',
  '13',
  '31',
  '16',
  '2',
  '2',
  '31',
  '2',
  '16.7',
  '15.1',
  '12.4',
  '27.5',
  '209',
  '449',
  '1.64',
  '1.18',
  '2.82',
  '1.45',
  '2.64',
  '1.52',
  '1.13',
  '2.65',
  '1.38',
  '2.50'],
 ['Atlético Madrid',
  '22',
  '29.7',
  '51.3',
  '11',
  '121',
  '990',
  '11.0',
  '26',
  '16',
  '42',


In [73]:
# Ahora saquemos los nombres de las columnas de la tabla de estadisticas de equipos. Se encuentran en columnas_html
# del elemento 0 al 31

columnas_tabla_equipos = []

for i in range(0,32):
    
    columnas_tabla_equipos.append(columnas_html[i].text)
    
columnas_tabla_equipos # lo dejamos por aqui porque es útil para buscar en el data frame

['Equipo',
 'PL',
 'Edad',
 'Pos.',
 'PJ',
 'Titular',
 'Mín',
 '90 s',
 'Gls.',
 'Ass',
 'G+A',
 'G-TP',
 'TP',
 'TPint',
 'TA',
 'TR',
 'xG',
 'npxG',
 'xAG',
 'npxG+xAG',
 'PrgC',
 'PrgP',
 'Gls.',
 'Ast',
 'G+A',
 'G-TP',
 'G+A-TP',
 'xG',
 'xAG',
 'xG+xAG',
 'npxG',
 'npxG+xAG']

In [74]:
# Creamos el Data Frame

df_equipos = pd.DataFrame(data_equipos, columns = columnas_tabla_equipos)
df_equipos

Equipo  PL  Edad  Pos.  PJ Titular    Mín  90 s Gls. Ass  ...  \
0            Alavés  22  26.9  44.0  11     121    990  11.0    7   7  ...   
1           Almería  27  25.6  48.4  11     121    990  11.0   14   9  ...   
2     Athletic Club  23  28.0  51.9  11     121    990  11.0   18  13  ...   
3   Atlético Madrid  22  29.7  51.3  11     121    990  11.0   26  16  ...   
4         Barcelona  24  26.6  65.6  12     132  1,080  12.0   23  15  ...   
5             Betis  29  28.5  52.8  12     132  1,080  12.0   16  11  ...   
6             Cádiz  25  29.5  38.3  11     121    990  11.0   10   6  ...   
7        Celta Vigo  24  26.8  43.1  12     132  1,080  12.0   10   7  ...   
8            Getafe  24  28.6  40.4  11     121    990  11.0   13  10  ...   
9            Girona  22  26.7  56.3  12     132  1,080  12.0   29  23  ...   
10          Granada  26  27.6  43.5  11     121    990  11.0   16  14  ...   
11       Las Palmas  24  26.6  57.9  12     132  1,080  12.0   10   5  ...   
12         Mallorca  21  28.8  41.8  12     132  1,080  12.0   12   9  ...   
13          Osasuna  22  28.3  48.0  12     132  1,080  12.0   14   8  ...   
14   Rayo Vallecano  22  30.3  47.7  11     121    990  11.0   14   7  ...   
15      Real Madrid  21  27.6  56.9  11     121    990  11.0   23  18  ...   
16    Real Sociedad  24  26.1  53.8  12     132  1,080  12.0   19  14  ...   
17          Sevilla  27  29.9  54.5  11     121    990  11.0   15   8  ...   
18         Valencia  24  24.4  47.5  11     121    990  11.0   14  10  ...   
19       Villarreal  24  28.2  54.5  11     121    990  11.0   15  10  ...   

    Gls.   Ast   G+A  G-TP G+A-TP    xG   xAG xG+xAG  npxG npxG+xAG  
0   0.64  0.64  1.27  0.64   1.27  1.23  0.86   2.09  1.15     2.02  
1   1.27  0.82  2.09  1.18   2.00  1.47  1.06   2.53  1.40     2.46  
2   1.64  1.18  2.82  1.45   2.64  1.52  1.13   2.65  1.38     2.50  
3   2.36  1.45  3.82  2.18   3.64  1.72  1.36   3.08  1.59     2.96  
4   1.92  1.25  3.17  1.83   3.08  2.11  1.50   3.60  2.04     3.54  
5   1.33  0.92  2.25  1.33   2.25  1.17  0.97   2.14  1.17     2.14  
6   0.91  0.55  1.45  0.82   1.36  0.86  0.54   1.41  0.79     1.34  
7   0.83  0.58  1.42  0.83   1.42  1.35  1.00   2.34  1.28     2.28  
8   1.18  0.91  2.09  1.00   1.91  0.96  0.61   1.57  0.81     1.42  
9   2.42  1.92  4.33  2.33   4.25  1.71  1.37   3.08  1.64     3.02  
10  1.45  1.27  2.73  1.27   2.55  1.28  0.92   2.20  1.06     1.99  
11  0.83  0.42  1.25  0.58   1.00  0.93  0.57   1.51  0.67     1.25  
12  1.00  0.75  1.75  0.92   1.67  1.15  0.78   1.93  0.96     1.74  
13  1.17  0.67  1.83  0.92   1.58  1.11  0.69   1.80  0.91     1.60  
14  1.27  0.64  1.91  0.82   1.45  1.46  0.72   2.18  1.10     1.82  
15  2.09  1.64  3.73  2.09   3.73  1.82  1.39   3.21  1.70     3.09  
16  1.58  1.17  2.75  1.42   2.58  1.31  0.93   2.24  1.17     2.11  
17  1.36  0.73  2.09  1.36   2.09  1.22  0.93   2.15  1.22     2.15  
18  1.27  0.91  2.18  1.18   2.09  1.10  0.76   1.86  1.03     1.79  
19  1.36  0.91  2.27  1.09   2.00  1.23  0.78   2.01  1.01     1.79  

[20 rows x 32 columns]

In [75]:
# Lo guardo en csvs para leerlo con R y hacer graficas en R
df_equipos.to_csv('df_equipos.txt', sep='\t', index=False)

In [76]:
df.to_csv('df_jugadores.txt', sep='\t', index=False)